# Capstone Project - The Battle of Neighborhoods 

## Business Problem section


Background


According to Bloomberg News, the London Housing Market is in a rut. It is now facing a number of different headwinds, including the prospect of higher taxes and a warning from the Bank of England that U.K. home values could fall as much as 30 percent in the event of a disorderly exit from the European Union. More specifically, four overlooked cracks suggest that the London market may be in worse shape than many realize: hidden price falls, record-low sales, homebuilder exodus and tax hikes addressing overseas buyers of homes in England and Wales.

Business Problem


In this scenario, it is urgent to adopt machine learning tools in order to assist homebuyers clientele in London to make wise and effective decisions. As a result, the business problem we are currently posing is: how could we provide support to homebuyers clientele in to purchase a suitable real estate in London in this uncertain economic and financial scenario?

To solve this business problem, we are going to cluster London neighborhoods in order to recommend venues and the current average price of real estate where homebuyers can make a real estate investment. We will recommend profitable venues according to amenities and essential facilities surrounding such venues i.e. elementary schools, high schools, hospitals & grocery stores.


Data section


Data on London properties and the relative price paid data were extracted from the HM Land Registry (http://landregistry.data.gov.uk/). The following fields comprise the address data included in Price Paid Data: Postcode; PAON Primary Addressable Object Name. Typically the house number or name; SAON Secondary Addressable Object Name. If there is a sub-building, for example, the building is divided into flats, there will be a SAON; Street; Locality; Town/City; District; County.

To explore and target recommended locations across different venues according to the presence of amenities and essential facilities, we will access data through FourSquare API interface and arrange them as a dataframe for visualization. By merging data on London properties and the relative price paid data from the HM Land Registry and data on amenities and essential facilities surrounding such properties from FourSquare API interface, we will be able to recommend profitable real estate investments.

 Methodology section
    
    
The Methodology section will describe the main components of our analysis and predication system. The Methodology section comprises four stages:

1. Collect Inspection Data
2. Explore and Understand Data
3. Data preparation and preprocessing 
4. Modeling


1. Collect Inspection Data
After importing the necessary libraries, we download the data from the HM Land Registry website as follows:

In [5]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files
!pip install folium
!pip install geopy
#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [6]:

#Read the data for examination (Source: http://landregistry.data.gov.uk/)
df_ppd = pd.read_csv("http://prod2.publicdata.landregistry.gov.uk.s3-website-eu-west-1.amazonaws.com/pp-2018.csv")

In [7]:
df_ppd.head(5)


{AE4D86D3-BE12-4619-E053-6C04A8C03CD0}  495000  2018-04-27 00:00   CM1 6BU  \
0  {AE4D86D3-BE1C-4619-E053-6C04A8C03CD0}  255000  2018-12-19 00:00   SS3 9DX   
1  {AE4D86D3-BF0C-4619-E053-6C04A8C03CD0}  195000  2018-10-12 00:00   CM7 3AT   
2  {AE4D86D3-BF10-4619-E053-6C04A8C03CD0}  445000  2018-11-30 00:00   CM9 8UA   
3  {AE4D86D3-BF20-4619-E053-6C04A8C03CD0}  600000  2018-05-14 00:00   CM9 6SX   
4  {AE4D86D3-BF2D-4619-E053-6C04A8C03CD0}  350000  2018-12-06 00:00  CO16 9FD   

   D  Y  F        64 Unnamed: 8 EDWARD HARVEY LINK       SPRINGFIELD  \
0  T  N  F        51        NaN       SEAVIEW ROAD      SHOEBURYNESS   
1  F  N  L         5        NaN      THE TILEWORKS               NaN   
2  S  N  F  THE ELMS          3    TOLLESBURY ROAD  TOLLESHUNT DARCY   
3  D  N  F  BIRCHLEY        NaN   POST OFFICE ROAD  WOODHAM MORTIMER   
4  D  N  F        10        NaN   WHITEGATES COURT    LITTLE CLACTON   

        CHELMSFORD     CHELMSFORD.1            ESSEX  A A.1  
0  SOUTHEND-ON-SEA  SOUTHEND-ON-SEA  SOUTHEND-ON-SEA  A   A  
1        BRAINTREE        BRAINTREE            ESSEX  A   A  
2           MALDON           MALDON            ESSEX  A   A  
3           MALDON           MALDON            ESSEX  A   A  
4   CLACTON-ON-SEA         TENDRING            ESSEX  A   A

In [8]:
df_ppd.shape

(1032582, 16)


Our dataset consists of over 700000 rows and 16 columns. We will now prepare and preprocess data accordingly.

3. Data preparation and preprocessing
At this stage, we prepare our dataset for the modeling process, opting for the most suitable machine learning algorithm for our scope. Accordingly, we perform the following steps:

Rename the column names
Format the date column
Sort data by date of sale
Select data only for the city of London
Make a list of street names in London
Calculate the street-wise average price of the property
Read the street-wise coordinates into a data frame, eliminating recurring word London from individual names
Join the data to find the coordinates of locations which fit into client's budget
Plot recommended locations on London map along with current market prices

In [9]:
# Assign meaningful column names
df_ppd.columns = ['TUID', 'Price', 'Date_Transfer', 'Postcode', 'Prop_Type', 'Old_New', 'Duration', 'PAON', \
                  'SAON', 'Street', 'Locality', 'Town_City', 'District', 'County', 'PPD_Cat_Type', 'Record_Status']

In [10]:

# Format the date column
df_ppd['Date_Transfer'] = df_ppd['Date_Transfer'].apply(pd.to_datetime)

# Delete all obsolete transactions which were done before 2016
df_ppd.drop(df_ppd[df_ppd.Date_Transfer.dt.year < 2016].index, inplace=True)

# Sort by Date of Sale
df_ppd.sort_values(by=['Date_Transfer'],ascending=[False],inplace=True)

In [34]:
df_ppd_london = df_ppd.query("Town_City == 'LONDON'")

# Make a list of street names in LONDON
streets = df_ppd_london['Street'].unique().tolist()

In [35]:

df_grp_price = df_ppd_london.groupby(['Street'])['Price'].mean().reset_index()

# Give meaningful names to the columns
df_grp_price.columns = ['Street', 'Avg_Price']

In [36]:
#Input your Budget's Upper Limit and Lower Limit - Find the locations df_grp_price which fits your budget
df_affordable = df_grp_price.query("(Avg_Price >= 2200000) & (Avg_Price <= 2500000)")

In [37]:

# Display the dataframe
df_affordable

Street     Avg_Price
196                ALBION SQUARE  2.450000e+06
390                  ANHALT ROAD  2.435000e+06
405              ANSDELL TERRACE  2.250000e+06
422              APPLEGARTH ROAD  2.400000e+06
857              BARONSMEAD ROAD  2.375000e+06
983               BEAUCLERC ROAD  2.480000e+06
1105             BELVEDERE DRIVE  2.340000e+06
1218           BICKENHALL STREET  2.208500e+06
1256           BIRCHLANDS AVENUE  2.217000e+06
1556              BRAMPTON GROVE  2.456875e+06
1635           BRIARDALE GARDENS  2.397132e+06
1800                    BROOKWAY  2.400000e+06
1983                   BURY WALK  2.492500e+06
2071             CALLCOTT STREET  2.375000e+06
2132           CAMPDEN HILL ROAD  2.379653e+06
2139                CAMPION ROAD  2.461000e+06
2161               CANNING PLACE  2.425000e+06
2228               CARLISLE ROAD  2.200000e+06
2233             CARLTON GARDENS  2.483500e+06
2245               CARLYLE COURT  2.300000e+06
2408              CHALCOT SQUARE  2.286679e+06
2486                CHARLES LANE  2.414000e+06
2564            CHELSEA CRESCENT  2.495000e+06
2608         CHESTER CLOSE NORTH  2.450000e+06
2640                CHEYNE COURT  2.250000e+06
2643                  CHEYNE ROW  2.410000e+06
2688               CHISWICK MALL  2.287500e+06
2763                   CITY ROAD  2.468340e+06
2810            CLARENDON STREET  2.250000e+06
2902            CLONCURRY STREET  2.388333e+06
2946                COLBECK MEWS  2.367500e+06
2997            COLLEGE CRESCENT  2.440000e+06
3204       CORNWALL TERRACE MEWS  2.350000e+06
3257          COURT LANE GARDENS  2.360000e+06
3379              CRESCENT GROVE  2.298000e+06
3585               DALEBURY ROAD  2.400000e+06
3850               DEWHURST ROAD  2.425000e+06
3931                  DORIA ROAD  2.362500e+06
3982              DOWNSHIRE HILL  2.225000e+06
4037                DUCHESS WALK  2.477500e+06
4234       ECCLESTON SQUARE MEWS  2.335500e+06
4287               EGBERT STREET  2.265000e+06
4291               EGERTON PLACE  2.200000e+06
4377               ELM PARK ROAD  2.320425e+06
4896               FLORAL STREET  2.227222e+06
5019             FRANK DIXON WAY  2.212500e+06
5101                 FULTON MEWS  2.299000e+06
5243                 GERARD ROAD  2.258500e+06
5246                GERRARD ROAD  2.242500e+06
5291               GIRDLERS ROAD  2.441667e+06
5384         GLOUCESTER CRESCENT  2.350833e+06
5453                GORDON PLACE  2.477000e+06
5489              GRAFTON SQUARE  2.270000e+06
5496              GRAHAM TERRACE  2.325000e+06
5956                HARMAN DRIVE  2.262500e+06
5980               HARRIS STREET  2.471769e+06
6044             HAVANNAH STREET  2.217309e+06
6116              HAZLEWELL ROAD  2.500000e+06
6232               HEREFORD MEWS  2.310000e+06
6252            HERONDALE AVENUE  2.475000e+06
6364               HIGHWOOD HILL  2.252500e+06
6400              HILLGATE PLACE  2.200000e+06
6511           HOLLYCROFT AVENUE  2.361375e+06
6515              HOLLYWOOD MEWS  2.350000e+06
6560              HONEYWELL ROAD  2.278333e+06
6616              HORTENSIA ROAD  2.275917e+06
6645               HOXTON SQUARE  2.234286e+06
6671                 HUNTER ROAD  2.300000e+06
6830               JACKSONS LANE  2.362500e+06
6890                 JOHN STREET  2.235000e+06
7196            KINNERTON STREET  2.485600e+06
7230         KNARESBOROUGH PLACE  2.325000e+06
7250                 KNOX STREET  2.250000e+06
7339              LANCASTER MEWS  2.312500e+06
7410              LANSDOWNE ROAD  2.364876e+06
7439   LATIMER INDUSTRIAL ESTATE  2.400000e+06
7492                LAXTON PLACE  2.500000e+06
7694              LINCOLN AVENUE  2.203500e+06
7723              LINGFIELD ROAD  2.248750e+06
7752               LISSON STREET  2.462500e+06
7786             LIVERPOOL GROVE  2.288000e+06
7879              LONGWOOD DRIVE  2.375000e+06
7885             LONSDALE SQUARE  2.357500e+06
8197            MANSFIELD STREET  2.500000e+06
8423                   MAZE HIL

In [38]:

import pandas as pd
import numpy as np
import datetime as DT
import hmac
from geopy.geocoders import Nominatim
from geopy.distance import vincenty
# import k-means from clustering stage
from sklearn.cluster import KMeans

In [59]:

for index, item in df_affordable.iterrows():
    print(f"index: {index}")
    print(f"item: {item}")
    print(f"item.Street only: {item.Street}")

index: 196
item: Street       ALBION SQUARE
Avg_Price         2.45e+06
Name: 196, dtype: object
item.Street only: ALBION SQUARE
index: 390
item: Street       ANHALT ROAD
Avg_Price      2.435e+06
Name: 390, dtype: object
item.Street only: ANHALT ROAD
index: 405
item: Street       ANSDELL TERRACE
Avg_Price           2.25e+06
Name: 405, dtype: object
item.Street only: ANSDELL TERRACE
index: 422
item: Street       APPLEGARTH ROAD
Avg_Price            2.4e+06
Name: 422, dtype: object
item.Street only: APPLEGARTH ROAD
index: 857
item: Street       BARONSMEAD ROAD
Avg_Price          2.375e+06
Name: 857, dtype: object
item.Street only: BARONSMEAD ROAD
index: 983
item: Street       BEAUCLERC ROAD
Avg_Price          2.48e+06
Name: 983, dtype: object
item.Street only: BEAUCLERC ROAD
index: 1105
item: Street       BELVEDERE DRIVE
Avg_Price           2.34e+06
Name: 1105, dtype: object
item.Street only: BELVEDERE DRIVE
index: 1218
item: Street       BICKENHALL STREET
Avg_Price           2.2085e+06
N

In [67]:
geolocator = Nominatim(user_agent="city_coord")

In [68]:

df_affordable['city_coord'] = df_affordable['Street'].apply(geolocator.geocode).apply(lambda x: (x.latitude, x.longitude))

<ipython-input-68-0f5362039c03>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_affordable['city_coord'] = df_affordable['Street'].apply(geolocator.geocode).apply(lambda x: (x.latitude, x.longitude))


In [69]:

df_affordable

Street     Avg_Price  \
196                ALBION SQUARE  2.450000e+06   
390                  ANHALT ROAD  2.435000e+06   
405              ANSDELL TERRACE  2.250000e+06   
422              APPLEGARTH ROAD  2.400000e+06   
857              BARONSMEAD ROAD  2.375000e+06   
983               BEAUCLERC ROAD  2.480000e+06   
1105             BELVEDERE DRIVE  2.340000e+06   
1218           BICKENHALL STREET  2.208500e+06   
1256           BIRCHLANDS AVENUE  2.217000e+06   
1556              BRAMPTON GROVE  2.456875e+06   
1635           BRIARDALE GARDENS  2.397132e+06   
1800                    BROOKWAY  2.400000e+06   
1983                   BURY WALK  2.492500e+06   
2071             CALLCOTT STREET  2.375000e+06   
2132           CAMPDEN HILL ROAD  2.379653e+06   
2139                CAMPION ROAD  2.461000e+06   
2161               CANNING PLACE  2.425000e+06   
2228               CARLISLE ROAD  2.200000e+06   
2233             CARLTON GARDENS  2.483500e+06   
2245               CARLYLE COURT  2.300000e+06   
2408              CHALCOT SQUARE  2.286679e+06   
2486                CHARLES LANE  2.414000e+06   
2564            CHELSEA CRESCENT  2.495000e+06   
2608         CHESTER CLOSE NORTH  2.450000e+06   
2640                CHEYNE COURT  2.250000e+06   
2643                  CHEYNE ROW  2.410000e+06   
2688               CHISWICK MALL  2.287500e+06   
2763                   CITY ROAD  2.468340e+06   
2810            CLARENDON STREET  2.250000e+06   
2902            CLONCURRY STREET  2.388333e+06   
2946                COLBECK MEWS  2.367500e+06   
2997            COLLEGE CRESCENT  2.440000e+06   
3204       CORNWALL TERRACE MEWS  2.350000e+06   
3257          COURT LANE GARDENS  2.360000e+06   
3379              CRESCENT GROVE  2.298000e+06   
3585               DALEBURY ROAD  2.400000e+06   
3850               DEWHURST ROAD  2.425000e+06   
3931                  DORIA ROAD  2.362500e+06   
3982              DOWNSHIRE HILL  2.225000e+06   
4037                DUCHESS WALK  2.477500e+06   
4234       ECCLESTON SQUARE MEWS  2.335500e+06   
4287               EGBERT STREET  2.265000e+06   
4291               EGERTON PLACE  2.200000e+06   
4377               ELM PARK ROAD  2.320425e+06   
4896               FLORAL STREET  2.227222e+06   
5019             FRANK DIXON WAY  2.212500e+06   
5101                 FULTON MEWS  2.299000e+06   
5243                 GERARD ROAD  2.258500e+06   
5246                GERRARD ROAD  2.242500e+06   
5291               GIRDLERS ROAD  2.441667e+06   
5384         GLOUCESTER CRESCENT  2.350833e+06   
5453                GORDON PLACE  2.477000e+06   
5489              GRAFTON SQUARE  2.270000e+06   
5496              GRAHAM TERRACE  2.325000e+06   
5956                HARMAN DRIVE  2.262500e+06   
5980               HARRIS STREET  2.471769e+06   
6044             HAVANNAH STREET  2.217309e+06   
6116              HAZLEWELL ROAD  2.500000e+06   
6232               HEREFORD MEWS  2.310000e+06   
6252            HERONDALE AVENUE  2.475000e+06   
6364               HIGHWOOD HILL  2.252500e+06   
6400              HILLGATE PLACE  2.200000e+06   
6511           HOLLYCROFT AVENUE  2.361375e+06   
6515              HOLLYWOOD MEWS  2.350000e+06   
6560              HONEYWELL ROAD  2.278333e+06   
6616              HORTENSIA ROAD  2.275917e+06   
6645               HOXTON SQUARE  2.234286e+06   
6671                 HUNTER ROAD  2.300000e+06   
6830               JACKSONS LANE  2.362500e+06   
6890                 JOHN STREET  2.235000e+06   
7196            KINNERTON STREET  2.485600e+06   
7230         KNARESBOROUGH PLACE  2.325000e+06   
7250                 KNOX STREET  2.250000e+06   
7339              LANCASTER MEWS  2.312500e+06   
7410              LANSDOWNE ROAD  2.364876e+06   
7439   LATIMER INDUSTRIAL ESTATE  2.400000e+06   
7492                LAXTON PLACE  2.500000e+06   
7694              LINCOLN AVENUE  2.203500e+06   
7723              LINGFIELD ROAD  2.248750e+06   
7752               LISSON 

In [70]:

df_affordable[['Latitude', 'Longitude']] = df_affordable['city_coord'].apply(pd.Series)

C:\Users\olaes\anaconda3\lib\site-packages\pandas\core\frame.py:3065: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[k1] = value[k2]


In [71]:
df_affordable

Street     Avg_Price  \
196                ALBION SQUARE  2.450000e+06   
390                  ANHALT ROAD  2.435000e+06   
405              ANSDELL TERRACE  2.250000e+06   
422              APPLEGARTH ROAD  2.400000e+06   
857              BARONSMEAD ROAD  2.375000e+06   
983               BEAUCLERC ROAD  2.480000e+06   
1105             BELVEDERE DRIVE  2.340000e+06   
1218           BICKENHALL STREET  2.208500e+06   
1256           BIRCHLANDS AVENUE  2.217000e+06   
1556              BRAMPTON GROVE  2.456875e+06   
1635           BRIARDALE GARDENS  2.397132e+06   
1800                    BROOKWAY  2.400000e+06   
1983                   BURY WALK  2.492500e+06   
2071             CALLCOTT STREET  2.375000e+06   
2132           CAMPDEN HILL ROAD  2.379653e+06   
2139                CAMPION ROAD  2.461000e+06   
2161               CANNING PLACE  2.425000e+06   
2228               CARLISLE ROAD  2.200000e+06   
2233             CARLTON GARDENS  2.483500e+06   
2245               CARLYLE COURT  2.300000e+06   
2408              CHALCOT SQUARE  2.286679e+06   
2486                CHARLES LANE  2.414000e+06   
2564            CHELSEA CRESCENT  2.495000e+06   
2608         CHESTER CLOSE NORTH  2.450000e+06   
2640                CHEYNE COURT  2.250000e+06   
2643                  CHEYNE ROW  2.410000e+06   
2688               CHISWICK MALL  2.287500e+06   
2763                   CITY ROAD  2.468340e+06   
2810            CLARENDON STREET  2.250000e+06   
2902            CLONCURRY STREET  2.388333e+06   
2946                COLBECK MEWS  2.367500e+06   
2997            COLLEGE CRESCENT  2.440000e+06   
3204       CORNWALL TERRACE MEWS  2.350000e+06   
3257          COURT LANE GARDENS  2.360000e+06   
3379              CRESCENT GROVE  2.298000e+06   
3585               DALEBURY ROAD  2.400000e+06   
3850               DEWHURST ROAD  2.425000e+06   
3931                  DORIA ROAD  2.362500e+06   
3982              DOWNSHIRE HILL  2.225000e+06   
4037                DUCHESS WALK  2.477500e+06   
4234       ECCLESTON SQUARE MEWS  2.335500e+06   
4287               EGBERT STREET  2.265000e+06   
4291               EGERTON PLACE  2.200000e+06   
4377               ELM PARK ROAD  2.320425e+06   
4896               FLORAL STREET  2.227222e+06   
5019             FRANK DIXON WAY  2.212500e+06   
5101                 FULTON MEWS  2.299000e+06   
5243                 GERARD ROAD  2.258500e+06   
5246                GERRARD ROAD  2.242500e+06   
5291               GIRDLERS ROAD  2.441667e+06   
5384         GLOUCESTER CRESCENT  2.350833e+06   
5453                GORDON PLACE  2.477000e+06   
5489              GRAFTON SQUARE  2.270000e+06   
5496              GRAHAM TERRACE  2.325000e+06   
5956                HARMAN DRIVE  2.262500e+06   
5980               HARRIS STREET  2.471769e+06   
6044             HAVANNAH STREET  2.217309e+06   
6116              HAZLEWELL ROAD  2.500000e+06   
6232               HEREFORD MEWS  2.310000e+06   
6252            HERONDALE AVENUE  2.475000e+06   
6364               HIGHWOOD HILL  2.252500e+06   
6400              HILLGATE PLACE  2.200000e+06   
6511           HOLLYCROFT AVENUE  2.361375e+06   
6515              HOLLYWOOD MEWS  2.350000e+06   
6560              HONEYWELL ROAD  2.278333e+06   
6616              HORTENSIA ROAD  2.275917e+06   
6645               HOXTON SQUARE  2.234286e+06   
6671                 HUNTER ROAD  2.300000e+06   
6830               JACKSONS LANE  2.362500e+06   
6890                 JOHN STREET  2.235000e+06   
7196            KINNERTON STREET  2.485600e+06   
7230         KNARESBOROUGH PLACE  2.325000e+06   
7250                 KNOX STREET  2.250000e+06   
7339              LANCASTER MEWS  2.312500e+06   
7410              LANSDOWNE ROAD  2.364876e+06   
7439   LATIMER INDUSTRIAL ESTATE  2.400000e+06   
7492                LAXTON PLACE  2.500000e+06   
7694              LINCOLN AVENUE  2.203500e+06   
7723              LINGFIELD ROAD  2.248750e+06   
7752               LISSON 

In [72]:
df = df_affordable.drop(columns=['city_coord'])

In [73]:
df

Street     Avg_Price   Latitude   Longitude
196                ALBION SQUARE  2.450000e+06 -41.273758  173.289393
390                  ANHALT ROAD  2.435000e+06  29.805547  -98.475534
405              ANSDELL TERRACE  2.250000e+06  51.500005   -0.189154
422              APPLEGARTH ROAD  2.400000e+06  40.271236  -74.471110
857              BARONSMEAD ROAD  2.375000e+06  51.477315   -0.239457
983               BEAUCLERC ROAD  2.480000e+06  30.207887  -81.628209
1105             BELVEDERE DRIVE  2.340000e+06 -29.580059   31.088130
1218           BICKENHALL STREET  2.208500e+06  51.521201   -0.158908
1256           BIRCHLANDS AVENUE  2.217000e+06  51.448414   -0.160457
1556              BRAMPTON GROVE  2.456875e+06  51.570365   -0.283394
1635           BRIARDALE GARDENS  2.397132e+06  51.560175   -0.195431
1800                    BROOKWAY  2.400000e+06  45.432185 -122.802812
1983                   BURY WALK  2.492500e+06  52.145529   -0.423593
2071             CALLCOTT STREET  2.375000e+06  51.508350   -0.198328
2132           CAMPDEN HILL ROAD  2.379653e+06  51.507025   -0.199145
2139                CAMPION ROAD  2.461000e+06  50.908982   -1.338778
2161               CANNING PLACE  2.425000e+06  51.499567   -0.184270
2228               CARLISLE ROAD  2.200000e+06  54.950286   -2.943244
2233             CARLTON GARDENS  2.483500e+06 -37.801943  144.971970
2245               CARLYLE COURT  2.300000e+06  32.972701  -97.173392
2408              CHALCOT SQUARE  2.286679e+06  51.540998   -0.155728
2486                CHARLES LANE  2.414000e+06  41.795422  -88.278844
2564            CHELSEA CRESCENT  2.495000e+06  51.477593   -0.181254
2608         CHESTER CLOSE NORTH  2.450000e+06  51.529205   -0.145081
2640                CHEYNE COURT  2.250000e+06  51.484603   -0.163820
2643                  CHEYNE ROW  2.410000e+06  51.483717   -0.169603
2688               CHISWICK MALL  2.287500e+06  51.487185   -0.248017
2763                   CITY ROAD  2.468340e+06  51.529697   -0.097763
2810            CLARENDON STREET  2.250000e+06  51.124152    1.303649
2902            CLONCURRY STREET  2.388333e+06  51.473763   -0.216244
2946                COLBECK MEWS  2.367500e+06  51.492964   -0.185972
2997            COLLEGE CRESCENT  2.440000e+06  37.235918  -76.707370
3204       CORNWALL TERRACE MEWS  2.350000e+06  51.524066   -0.157667
3257          COURT LANE GARDENS  2.360000e+06  51.448500   -0.080102
3379              CRESCENT GROVE  2.298000e+06  46.115586  -60.725330
3585               DALEBURY ROAD  2.400000e+06  51.439155   -0.165075
3850               DEWHURST ROAD  2.425000e+06  51.498467   -0.219229
3931                  DORIA ROAD  2.362500e+06  51.473116   -0.201748
3982              DOWNSHIRE HILL  2.225000e+06  51.555662   -0.170293
4037                DUCHESS WALK  2.477500e+06  51.503801   -0.076921
4234       ECCLESTON SQUARE MEWS  2.335500e+06  51.491798   -0.142943
4287               EGBERT STREET  2.265000e+06  51.540469   -0.152987
4291               EGERTON PLACE  2.200000e+06  51.496695   -0.167068
4377               ELM PARK ROAD  2.320425e+06  49.856103  -97.117790
4896               FLORAL STREET  2.227222e+06  28.568165  -81.545839
5019             FRANK DIXON WAY  2.212500e+06  51.443816   -0.082265
5101                 FULTON MEWS  2.299000e+06  51.512495   -0.185095
5243                 GERARD ROAD  2.258500e+06  51.805800    1.135193
5246                GERRARD ROAD  2.242500e+06  54.889253   -1.446589
5291               GIRDLERS ROAD  2.441667e+06  51.496697   -0.215531
5384         GLOUCESTER CRESCENT  2.350833e+06  49.631065 -118.395333
5453                GORDON PLACE  2.477000e+06  41.608524  -93.609850
5489              GRAFTON SQUARE  2.270000e+06  51.463987   -0.139082
5496              GRAHAM TERRACE  2.325000e+06  51.491547   -0.154275
5956                HARMAN DRIVE  2.262500e+06  51.448159    0.096598
5980               HARRIS STREET  2.471769e+06  30.413176  -86.732940
6044             HAVANNAH STREET  2.

In [79]:
address = 'London, UK'

geolocator = Nominatim(user_agent="location")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of London City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of London City are 51.5073219, -0.1276474.


In [80]:
# create map of London using latitude and longitude values
map_london = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, price, street in zip(df['Latitude'], df['Longitude'], df['Avg_Price'], df['Street']):
    label = '{}, {}'.format(street, price)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london)  
    
map_london

In [81]:
#Define Foursquare Credentials and Version

CLIENT_ID = 'KI3TR0QO4JOKMFELOMF3WSOOI3HFNBF5YLW354MYWBKDHEX3' # Foursquare ID
CLIENT_SECRET = 'QF4ZBLJRBV4BQX52DVWUPEHJ14A2UJABPCZARZQZYTKIISUD' # Foursquare Secret
VERSION = '20181206' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)


Your credentails:
CLIENT_ID: KI3TR0QO4JOKMFELOMF3WSOOI3HFNBF5YLW354MYWBKDHEX3
CLIENT_SECRET:QF4ZBLJRBV4BQX52DVWUPEHJ14A2UJABPCZARZQZYTKIISUD


We can now proceed to the Modeling phase. We will analyze neighborhoods to recommend real estates where home buyers can make a real estate investment. We will then recommend profitable venues according to amenities and essential facilities surrounding such venues i.e. elementary schools, high schools, hospitals & grocery stores.

###### 4. Modeling


After exploring the dataset and gaining insights into it, we are ready to use the clustering methodology to analyze real estates. We will use the k-means clustering technique as it is fast and efficient in terms of computational cost, is highly flexible to account for mutations in real estate market in London and is accurate.

In [82]:
def getNearbyVenues(names, latitudes, longitudes, radius=500, LIMIT=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Street', 
                  'Street Latitude', 
                  'Street Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [83]:

# Run the above function on each location and create a new dataframe called location_venues and display it.
location_venues = getNearbyVenues(names=df['Street'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

ALBION SQUARE
ANHALT ROAD
ANSDELL TERRACE
APPLEGARTH ROAD
BARONSMEAD ROAD
BEAUCLERC ROAD
BELVEDERE DRIVE
BICKENHALL STREET
BIRCHLANDS AVENUE
BRAMPTON GROVE
BRIARDALE GARDENS
BROOKWAY
BURY WALK
CALLCOTT STREET
CAMPDEN HILL ROAD
CAMPION ROAD
CANNING PLACE
CARLISLE ROAD
CARLTON GARDENS
CARLYLE COURT
CHALCOT SQUARE
CHARLES LANE
CHELSEA CRESCENT
CHESTER CLOSE NORTH
CHEYNE COURT
CHEYNE ROW
CHISWICK MALL
CITY ROAD
CLARENDON STREET
CLONCURRY STREET
COLBECK MEWS
COLLEGE CRESCENT
CORNWALL TERRACE MEWS
COURT LANE GARDENS
CRESCENT GROVE
DALEBURY ROAD
DEWHURST ROAD
DORIA ROAD
DOWNSHIRE HILL
DUCHESS WALK
ECCLESTON SQUARE MEWS
EGBERT STREET
EGERTON PLACE
ELM PARK ROAD
FLORAL STREET
FRANK DIXON WAY
FULTON MEWS
GERARD ROAD
GERRARD ROAD
GIRDLERS ROAD
GLOUCESTER CRESCENT
GORDON PLACE
GRAFTON SQUARE
GRAHAM TERRACE
HARMAN DRIVE
HARRIS STREET
HAVANNAH STREET
HAZLEWELL ROAD
HEREFORD MEWS
HERONDALE AVENUE
HIGHWOOD HILL
HILLGATE PLACE
HOLLYCROFT AVENUE
HOLLYWOOD MEWS
HONEYWELL ROAD
HORTENSIA ROAD
HOXTON SQUARE

In [84]:
location_venues

Street  Street Latitude  Street Longitude  \
0                 ALBION SQUARE       -41.273758        173.289393   
1                 ALBION SQUARE       -41.273758        173.289393   
2                 ALBION SQUARE       -41.273758        173.289393   
3                 ALBION SQUARE       -41.273758        173.289393   
4                 ALBION SQUARE       -41.273758        173.289393   
5                 ALBION SQUARE       -41.273758        173.289393   
6                 ALBION SQUARE       -41.273758        173.289393   
7                 ALBION SQUARE       -41.273758        173.289393   
8                 ALBION SQUARE       -41.273758        173.289393   
9                 ALBION SQUARE       -41.273758        173.289393   
10                ALBION SQUARE       -41.273758        173.289393   
11                ALBION SQUARE       -41.273758        173.289393   
12                ALBION SQUARE       -41.273758        173.289393   
13                ALBION SQUARE       -41.273758        173.289393   
14                ALBION SQUARE       -41.273758        173.289393   
15                ALBION SQUARE       -41.273758        173.289393   
16                ALBION SQUARE       -41.273758        173.289393   
17                ALBION SQUARE       -41.273758        173.289393   
18                ALBION SQUARE       -41.273758        173.289393   
19                ALBION SQUARE       -41.273758        173.289393   
20                ALBION SQUARE       -41.273758        173.289393   
21                ALBION SQUARE       -41.273758        173.289393   
22                ALBION SQUARE       -41.273758        173.289393   
23                ALBION SQUARE       -41.273758        173.289393   
24                ALBION SQUARE       -41.273758        173.289393   
25              ANSDELL TERRACE        51.500005         -0.189154   
26              ANSDELL TERRACE        51.500005         -0.189154   
27              ANSDELL TERRACE        51.500005         -0.189154   
28              ANSDELL TERRACE        51.500005         -0.189154   
29              ANSDELL TERRACE        51.500005         -0.189154   
30              ANSDELL TERRACE        51.500005         -0.189154   
31              ANSDELL TERRACE        51.500005         -0.189154   
32              ANSDELL TERRACE        51.500005         -0.189154   
33              ANSDELL TERRACE        51.500005         -0.189154   
34              ANSDELL TERRACE        51.500005         -0.189154   
35              ANSDELL TERRACE        51.500005         -0.189154   
36              ANSDELL TERRACE        51.500005         -0.189154   
37              ANSDELL TERRACE        51.500005         -0.189154   
38              ANSDELL TERRACE        51.500005         -0.189154   
39              ANSDELL TERRACE        51.500005         -0.189154   
40              ANSDELL TERRACE        51.500005         -0.189154   
41              ANSDELL TERRACE        51.500005         -0.189154   
42              ANSDELL TERRACE        51.500005         -0.189154   
43              ANSDELL TERRACE        51.500005         -0.189154   
44              ANSDELL TERRACE        51.500005         -0.189154   
45              ANSDELL TERRACE        51.500005         -0.189154   
46              ANSDELL TERRACE        51.500005         -0.189154   
47              ANSDELL TERRACE        51.500005         -0.189154   
48              ANSDELL TERRACE        51.500005         -0.189154   
49              ANSDELL TERRACE        51.500005         -0.189154   
50              ANSDELL TERRACE        51.500005         -0.189154   
51              ANSDELL TERRACE        51.500005         -0.189154   
52              ANSDELL TERRACE        51.500005         -0.189154   
53              ANSDELL TERRACE        51.500005         -0.189154   
54              ANSDELL TERRACE        51.500005         -0.189154   
55              ANSDELL TERRACE        51.500005         -0.189154   
56              ANSDELL TERRACE    

In [85]:
location_venues.groupby('Street').count()

Street Latitude  Street Longitude  Venue  \
Street                                                                
ALBION SQUARE                           25                25     25   
ANSDELL TERRACE                         69                69     69   
APPLEGARTH ROAD                          4                 4      4   
BARONSMEAD ROAD                         14                14     14   
BEAUCLERC ROAD                           1                 1      1   
BELVEDERE DRIVE                          1                 1      1   
BICKENHALL STREET                       62                62     62   
BIRCHLANDS AVENUE                       10                10     10   
BRAMPTON GROVE                           2                 2      2   
BRIARDALE GARDENS                        6                 6      6   
BROOKWAY                                 1                 1      1   
BURY WALK                               16                16     16   
CALLCOTT STREET                         48                48     48   
CAMPDEN HILL ROAD                       52                52     52   
CAMPION ROAD                             5                 5      5   
CANNING PLACE                           37                37     37   
CARLISLE ROAD                            4                 4      4   
CARLTON GARDENS                         58                58     58   
CARLYLE COURT                            1                 1      1   
CHALCOT SQUARE                          50                50     50   
CHARLES LANE                             5                 5      5   
CHELSEA CRESCENT                        25                25     25   
CHESTER CLOSE NORTH                     23                23     23   
CHEYNE COURT                            45                45     45   
CHEYNE ROW                              55                55     55   
CHISWICK MALL                            6                 6      6   
CITY ROAD                               30                30     30   
CLARENDON STREET                         4                 4      4   
CLONCURRY STREET                        30                30     30   
COLBECK MEWS                           100               100    100   
CORNWALL TERRACE MEWS                   50                50     50   
COURT LANE GARDENS                      15                15     15   
CRESCENT GROVE                           1                 1      1   
DALEBURY ROAD                           10                10     10   
DEWHURST ROAD                           29                29     29   
DORIA ROAD                              63                63     63   
DOWNSHIRE HILL                          37                37     37   
DUCHESS WALK                           100               100    100   
ECCLESTON SQUARE MEWS                  100               100    100   
EGBERT STREET                           48                48     48   
EGERTON PLACE                           92                92     92   
ELM PARK ROAD                            5                 5      5   
FLORAL STREET                            8                 8      8   
FRANK DIXON WAY                         10                10     10   
FULTON MEWS                             90                90     90   
GERARD ROAD                              3                 3      3   
GERRARD ROAD                             3                 3      3   
GIRDLERS ROAD                           35                35     35   
GORDON PLACE                             5                 5      5   
GRAFTON SQUARE                          81                81     81   
GRAHAM TERRACE                          69                69     69   
HARMAN DRIVE                             4                 4      4   
HARRIS STREET                            1                 1      1   
HAVANNAH STREET                         54                54     54   
HAZLEWELL ROAD                           7         

In [86]:

# get the List of Unique Categories
print('There are {} uniques categories.'.format(len(location_venues['Venue Category'].unique())))

There are 342 uniques categories.


In [87]:

location_venues.shape

(5018, 7)

In [88]:
# one hot encoding
venues_onehot = pd.get_dummies(location_venues[['Venue Category']], prefix="", prefix_sep="")

# add street column back to dataframe
venues_onehot['Street'] = location_venues['Street'] 

# move street column to the first column
fixed_columns = [venues_onehot.columns[-1]] + list(venues_onehot.columns[:-1])

#fixed_columns
venues_onehot = venues_onehot[fixed_columns]

venues_onehot.head()

Street  ATM  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  ALBION SQUARE    0                  0               0                  0   
1  ALBION SQUARE    0                  0               0                  0   
2  ALBION SQUARE    0                  0               0                  0   
3  ALBION SQUARE    0                  0               0                  0   
4  ALBION SQUARE    0                  0               0                  0   

   African Restaurant  Airport Service  American Restaurant  Antique Shop  \
0                   0                0                    0             0   
1                   0                0                    0             0   
2                   0                0                    0             0   
3                   0                0                    0             0   
4                   0                0                    0             0   

   Arcade  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                       0            0           0   
1       0                       0            0           0   
2       0                       0            0           0   
3       0                       0            0           0   
4       0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0                    0                 0                   0   
1                    0                 0                   0   
2                    0                 0                   0   
3                    0                 0                   0   
4                    0                 0                   0   

   Australian Restaurant  Austrian Restaurant  Auto Workshop  Automotive Shop  \
0                      0                    0              0                0   
1                      0                    0              0                0   
2                      0                    0              0                0   
3                      0                    0              0                0   
4                      0                    0              0                0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Basketball Court  \
0          0           0           0       0     0    1                 0   
1          0           0           0       0     0    0                 0   
2          0           0           0       0     0    0                 0   
3          0           0           0       0     0    0                 0   
4          0           0           0       0     0    0                 0   

   Bathing Area  Bay  Beach  Bed & Breakfast  Beer Bar  Beer Garden  \
0             0    0      0                0         0            0   
1             0    0      0                0         0            0   
2             0    0      0                0         0            0   
3             0    0      0                0         0            0   
4             0    0      0                0         0            0   

   Beer Store  Big Box Store  Bike Rental / Bike Share  Bike Shop  Bistro  \
0           0              0                         0          0       0   
1           0              0                         0          0       0   
2           0              0                         0          0       0   
3           0              0                         0          0       0   
4           0              0                         0          0       0   

   Boat or Ferry  Bookstore  Botanical Garden  Boutique  Bowling Green  \
0              0          0                 0         0              0   
1              0          0                 0         0              0   
2              0          0                 0         0              0   
3              0          0                 0         0              0   
4              0          0                 0         0              0   

   Boxing Gym  Brazilian Rest

In [89]:
london_grouped = venues_onehot.groupby('Street').mean().reset_index()
london_grouped

Street   ATM  Accessories Store  Adult Boutique  \
0                ALBION SQUARE  0.00           0.000000            0.00   
1              ANSDELL TERRACE  0.00           0.000000            0.00   
2              APPLEGARTH ROAD  0.00           0.000000            0.00   
3              BARONSMEAD ROAD  0.00           0.000000            0.00   
4               BEAUCLERC ROAD  0.00           0.000000            0.00   
5              BELVEDERE DRIVE  0.00           0.000000            0.00   
6            BICKENHALL STREET  0.00           0.000000            0.00   
7            BIRCHLANDS AVENUE  0.00           0.000000            0.00   
8               BRAMPTON GROVE  0.00           0.000000            0.00   
9            BRIARDALE GARDENS  0.00           0.000000            0.00   
10                    BROOKWAY  0.00           0.000000            0.00   
11                   BURY WALK  0.00           0.000000            0.00   
12             CALLCOTT STREET  0.00           0.000000            0.00   
13           CAMPDEN HILL ROAD  0.00           0.000000            0.00   
14                CAMPION ROAD  0.00           0.000000            0.00   
15               CANNING PLACE  0.00           0.000000            0.00   
16               CARLISLE ROAD  0.00           0.000000            0.00   
17             CARLTON GARDENS  0.00           0.000000            0.00   
18               CARLYLE COURT  0.00           0.000000            0.00   
19              CHALCOT SQUARE  0.00           0.000000            0.00   
20                CHARLES LANE  0.00           0.000000            0.00   
21            CHELSEA CRESCENT  0.00           0.000000            0.00   
22         CHESTER CLOSE NORTH  0.00           0.000000            0.00   
23                CHEYNE COURT  0.00           0.000000            0.00   
24                  CHEYNE ROW  0.00           0.018182            0.00   
25               CHISWICK MALL  0.00           0.000000            0.00   
26                   CITY ROAD  0.00           0.000000            0.00   
27            CLARENDON STREET  0.00           0.000000            0.00   
28            CLONCURRY STREET  0.00           0.000000            0.00   
29                COLBECK MEWS  0.00           0.000000            0.00   
30       CORNWALL TERRACE MEWS  0.00           0.000000            0.00   
31          COURT LANE GARDENS  0.00           0.000000            0.00   
32              CRESCENT GROVE  0.00           0.000000            0.00   
33               DALEBURY ROAD  0.00           0.000000            0.00   
34               DEWHURST ROAD  0.00           0.000000            0.00   
35                  DORIA ROAD  0.00           0.000000            0.00   
36              DOWNSHIRE HILL  0.00           0.000000            0.00   
37                DUCHESS WALK  0.00           0.000000            0.00   
38       ECCLESTON SQUARE MEWS  0.00           0.000000            0.00   
39               EGBERT STREET  0.00           0.000000            0.00   
40               EGERTON PLACE  0.00           0.000000            0.00   
41               ELM PARK ROAD  0.00           0.000000            0.00   
42               FLORAL STREET  0.00           0.000000            0.00   
43             FRANK DIXON WAY  0.00           0.000000            0.00   
44                 FULTON MEWS  0.00           0.000000            0.00   
45                 GERARD ROAD  0.00           0.000000            0.00   
46                GERRARD ROAD  0.00           0.000000            0.00   
47               GIRDLERS ROAD  0.00           0.000000            0.00   
48                GORDON PLACE  0.00           0.000000            0.00   
49              GRAFTON SQUARE  0.00           0.000000            0.00   
50              GRAHAM TERRACE  0.00           0.000000            0.00   
51                HARMAN DRIVE  0.00           0.000000            0.00   
52               HARRIS STREET  0.00           0.

In [90]:

london_grouped.shape

(148, 343)

In [91]:

# What are the top 5 venues/facilities nearby profitable real estate investments?#

num_top_venues = 5

for hood in london_grouped['Street']:
    print("----"+hood+"----")
    temp = london_grouped[london_grouped['Street'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----ALBION SQUARE----
               venue  freq
0               Café  0.20
1  Indian Restaurant  0.08
2                Bar  0.08
3         Restaurant  0.08
4                Pub  0.08


----ANSDELL TERRACE----
                venue  freq
0  Italian Restaurant  0.07
1               Hotel  0.07
2                 Pub  0.07
3   Indian Restaurant  0.06
4                Café  0.06


----APPLEGARTH ROAD----
                  venue  freq
0     Convenience Store  0.25
1            Donut Shop  0.25
2      Storage Facility  0.25
3  Fast Food Restaurant  0.25
4                   ATM  0.00


----BARONSMEAD ROAD----
               venue  freq
0  Food & Drink Shop  0.14
1    Nature Preserve  0.07
2   Community Center  0.07
3    Thai Restaurant  0.07
4     Farmers Market  0.07


----BEAUCLERC ROAD----
                           venue  freq
0        Health & Beauty Service   1.0
1                            ATM   0.0
2                        Parking   0.0
3  Paper / Office Supplies Store   0.0
4       

In [92]:

# Define a function to return the most common venues/facilities nearby real estate investments#

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [93]:

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Street']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

In [94]:

# create a new dataframe
venues_sorted = pd.DataFrame(columns=columns)
venues_sorted['Street'] = london_grouped['Street']

for ind in np.arange(london_grouped.shape[0]):
    venues_sorted.iloc[ind, 1:] = return_most_common_venues(london_grouped.iloc[ind, :], num_top_venues)

In [95]:
venues_sorted.head()

Street    1st Most Common Venue 2nd Most Common Venue  \
0    ALBION SQUARE                     Café     Indian Restaurant   
1  ANSDELL TERRACE                      Pub                 Hotel   
2  APPLEGARTH ROAD        Convenience Store            Donut Shop   
3  BARONSMEAD ROAD        Food & Drink Shop         Movie Theater   
4   BEAUCLERC ROAD  Health & Beauty Service           Zoo Exhibit   

         3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                          Pub                   Bar            Restaurant   
1           Italian Restaurant     Indian Restaurant            Restaurant   
2             Storage Facility  Fast Food Restaurant                  Farm   
3                         Park        Farmers Market            Restaurant   
4  Eastern European Restaurant     Electronics Store    English Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Breakfast Spot           Coffee Shop                Museum   
1                  Café             Juice Bar     French Restaurant   
2     Electronics Store    English Restaurant           Escape Room   
3       Thai Restaurant           Coffee Shop       Nature Preserve   
4           Escape Room           Event Space               Exhibit   

  9th Most Common Venue 10th Most Common Venue  
0     Fish & Chips Shop      French Restaurant  
1                Garden          Grocery Store  
2           Event Space                Exhibit  
3   Indie Movie Theater       Community Center  
4               Factory     Falafel Restaurant

In [96]:
venues_sorted.shape

(148, 11)

In [97]:
london_grouped.shape

(148, 343)

In [98]:
london_grouped=df


After our inspection of venues/facilities/amenities nearby the most profitable real estate investments in London, we could begin by clustering properties by venues/facilities/amenities nearby.

In [99]:
#Distribute in 5 Clusters

# set number of clusters
kclusters = 5

london_grouped_clustering = london_grouped.drop('Street', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(london_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:50]

array([1, 4, 2, 4, 0, 1, 0, 2, 2, 1, 4, 4, 1, 0, 0, 1, 4, 2, 1, 3, 3, 4,
       1, 1, 2, 4, 3, 1, 2, 4, 0, 4, 0, 0, 3, 4, 4, 0, 2, 1, 0, 3, 2, 3,
       2, 2, 3, 2, 2, 4])

In [100]:

#Dataframe to include Clusters

london_grouped_clustering=df
london_grouped_clustering.head()

Street  Avg_Price   Latitude   Longitude
196    ALBION SQUARE  2450000.0 -41.273758  173.289393
390      ANHALT ROAD  2435000.0  29.805547  -98.475534
405  ANSDELL TERRACE  2250000.0  51.500005   -0.189154
422  APPLEGARTH ROAD  2400000.0  40.271236  -74.471110
857  BARONSMEAD ROAD  2375000.0  51.477315   -0.239457

In [101]:
london_grouped_clustering.shape

(159, 4)

In [102]:
df.shape

(159, 4)

In [ ]:
london_grouped_clustering.dtypes

In [103]:

df.dtypes

Street        object
Avg_Price    float64
Latitude     float64
Longitude    float64
dtype: object

In [104]:
# add clustering labels
london_grouped_clustering['Cluster Labels'] = kmeans.labels_

# merge london_grouped with london_data to add latitude/longitude for each neighborhood
london_grouped_clustering = london_grouped_clustering.join(venues_sorted.set_index('Street'), on='Street')

london_grouped_clustering.head(30) # check the last columns!

Street     Avg_Price   Latitude   Longitude  \
196         ALBION SQUARE  2.450000e+06 -41.273758  173.289393   
390           ANHALT ROAD  2.435000e+06  29.805547  -98.475534   
405       ANSDELL TERRACE  2.250000e+06  51.500005   -0.189154   
422       APPLEGARTH ROAD  2.400000e+06  40.271236  -74.471110   
857       BARONSMEAD ROAD  2.375000e+06  51.477315   -0.239457   
983        BEAUCLERC ROAD  2.480000e+06  30.207887  -81.628209   
1105      BELVEDERE DRIVE  2.340000e+06 -29.580059   31.088130   
1218    BICKENHALL STREET  2.208500e+06  51.521201   -0.158908   
1256    BIRCHLANDS AVENUE  2.217000e+06  51.448414   -0.160457   
1556       BRAMPTON GROVE  2.456875e+06  51.570365   -0.283394   
1635    BRIARDALE GARDENS  2.397132e+06  51.560175   -0.195431   
1800             BROOKWAY  2.400000e+06  45.432185 -122.802812   
1983            BURY WALK  2.492500e+06  52.145529   -0.423593   
2071      CALLCOTT STREET  2.375000e+06  51.508350   -0.198328   
2132    CAMPDEN HILL ROAD  2.379653e+06  51.507025   -0.199145   
2139         CAMPION ROAD  2.461000e+06  50.908982   -1.338778   
2161        CANNING PLACE  2.425000e+06  51.499567   -0.184270   
2228        CARLISLE ROAD  2.200000e+06  54.950286   -2.943244   
2233      CARLTON GARDENS  2.483500e+06 -37.801943  144.971970   
2245        CARLYLE COURT  2.300000e+06  32.972701  -97.173392   
2408       CHALCOT SQUARE  2.286679e+06  51.540998   -0.155728   
2486         CHARLES LANE  2.414000e+06  41.795422  -88.278844   
2564     CHELSEA CRESCENT  2.495000e+06  51.477593   -0.181254   
2608  CHESTER CLOSE NORTH  2.450000e+06  51.529205   -0.145081   
2640         CHEYNE COURT  2.250000e+06  51.484603   -0.163820   
2643           CHEYNE ROW  2.410000e+06  51.483717   -0.169603   
2688        CHISWICK MALL  2.287500e+06  51.487185   -0.248017   
2763            CITY ROAD  2.468340e+06  51.529697   -0.097763   
2810     CLARENDON STREET  2.250000e+06  51.124152    1.303649   
2902     CLONCURRY STREET  2.388333e+06  51.473763   -0.216244   

      Cluster Labels       1st Most Common Venue        2nd Most Common Venue  \
196                1                        Café            Indian Restaurant   
390                4                         NaN                          NaN   
405                2                         Pub                        Hotel   
422                4           Convenience Store                   Donut Shop   
857                0           Food & Drink Shop                Movie Theater   
983                1     Health & Beauty Service                  Zoo Exhibit   
1105               0           Convenience Store         Fast Food Restaurant   
1218               2                  Restaurant                  Coffee Shop   
1256               2                         Pub                  Pizza Place   
1556               1                        Lake    Middle Eastern Restaurant   
1635               4           Convenience Store                  Coffee Shop   
1800               4                 Art Gallery  Eastern European Restaurant   
1983               1                 Supermarket           English Restaurant   
2071               0                         Pub                  Coffee Shop   
2132               0                 Coffee Shop                          Pub   
2139               1  Construction & Landscaping       Furniture / Home Store   
2161               4                       Hotel           Italian Restaurant   
2228               2                  Campground                         Café   
2233               1          Italian Restaurant                         Café   
2245               3                        Farm                  Zoo Exhibit   
2408               3                         Pub                         Café   
2486               4         Sporting Goods Shop                   Toll Booth   
2564               1                       Hotel                         Café   
2608               1        

In [105]:

# Create Map

map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(london_grouped_clustering['Latitude'], london_grouped_clustering['Longitude'], london_grouped_clustering['Street'], london_grouped_clustering['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [106]:

london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 0, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
857   2375000.0     Food & Drink Shop         Movie Theater   
1105  2340000.0     Convenience Store  Fast Food Restaurant   
2071  2375000.0                   Pub           Coffee Shop   
2132  2379652.7           Coffee Shop                   Pub   
2946  2367500.0                 Hotel                   Pub   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
857                   Park        Farmers Market            Restaurant   
1105    English Restaurant           Escape Room           Event Space   
2071                  Park        Ice Cream Shop           Yoga Studio   
2132                  Park         Grocery Store           Yoga Studio   
2946                Garden                  Café           Coffee Shop   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
857        Thai Restaurant           Coffee Shop       Nature Preserve   
1105               Exhibit               Factory    Falafel Restaurant   
2071         Grocery Store     Indian Restaurant           Pizza Place   
2132           Pizza Place     Indian Restaurant        Ice Cream Shop   
2946    Chinese Restaurant    Italian Restaurant     Indian Restaurant   

         9th Most Common Venue 10th Most Common Venue  
857        Indie Movie Theater       Community Center  
1105                      Farm         Farmers Market  
2071                     Hotel   Caribbean Restaurant  
2132            Sandwich Place                  Hotel  
2946  Mediterranean Restaurant                    Bar

In [107]:

london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 1, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price       1st Most Common Venue      2nd Most Common Venue  \
196   2450000.0                        Café          Indian Restaurant   
983   2480000.0     Health & Beauty Service                Zoo Exhibit   
1556  2456875.0                        Lake  Middle Eastern Restaurant   
1983  2492500.0                 Supermarket         English Restaurant   
2139  2461000.0  Construction & Landscaping     Furniture / Home Store   

            3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
196                           Pub                   Bar            Restaurant   
983   Eastern European Restaurant     Electronics Store    English Restaurant   
1556                  Zoo Exhibit        Farmers Market    English Restaurant   
1983                         Park   Rental Car Location        Discount Store   
2139                  Coffee Shop                Bakery  Fast Food Restaurant   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
196         Breakfast Spot           Coffee Shop                Museum   
983            Escape Room           Event Space               Exhibit   
1556           Escape Room           Event Space               Exhibit   
1983                   Gym        Hardware Store           Coffee Shop   
2139        Farmers Market    English Restaurant           Escape Room   

     9th Most Common Venue 10th Most Common Venue  
196      Fish & Chips Shop      French Restaurant  
983                Factory     Falafel Restaurant  
1556               Factory     Falafel Restaurant  
1983                  Café                    Pub  
2139           Event Space                Exhibit

In [108]:

london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 2, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
405   2250000.0                   Pub                 Hotel   
1218  2208500.0            Restaurant           Coffee Shop   
1256  2217000.0                   Pub           Pizza Place   
2228  2200000.0            Campground                  Café   
2640  2250000.0                   Pub                  Café   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
405     Italian Restaurant     Indian Restaurant            Restaurant   
1218             Gastropub         Movie Theater    Chinese Restaurant   
1256         Train Station                Bakery               Brewery   
2228       Bed & Breakfast            Food Court           Escape Room   
2640    English Restaurant           Coffee Shop         Grocery Store   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
405                   Café             Juice Bar     French Restaurant   
1218                   Bar                Garden    Italian Restaurant   
1256    Chinese Restaurant     French Restaurant                  Lake   
2228           Event Space               Exhibit               Factory   
2640                 Plaza     French Restaurant                Garden   

     9th Most Common Venue 10th Most Common Venue  
405                 Garden          Grocery Store  
1218      Greek Restaurant         Sandwich Place  
1256           Coffee Shop     English Restaurant  
2228    Falafel Restaurant                   Farm  
2640           Supermarket              Bookstore

In [109]:

london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 3, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue 2nd Most Common Venue  \
2245  2.300000e+06                  Farm           Zoo Exhibit   
2408  2.286679e+06                   Pub                  Café   
2688  2.287500e+06                   Pub               Brewery   
3379  2.298000e+06                 Hotel           Zoo Exhibit   
4287  2.265000e+06           Coffee Shop                  Café   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2245        Farmers Market     Electronics Store    English Restaurant   
2408    Italian Restaurant           Coffee Shop                   Bar   
2688             Gift Shop             Reservoir            Art Museum   
3379        Farmers Market     Electronics Store    English Restaurant   
4287                   Pub           Music Venue           Yoga Studio   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
2245           Escape Room           Event Space               Exhibit   
2408     French Restaurant                  Park          Cocktail Bar   
2688          Fishing Spot    Falafel Restaurant           Flower Shop   
3379           Escape Room           Event Space               Exhibit   
4287     French Restaurant    Italian Restaurant                Market   

     9th Most Common Venue 10th Most Common Venue  
2245               Factory     Falafel Restaurant  
2408            Restaurant         Ice Cream Shop  
2688     Electronics Store     English Restaurant  
3379               Factory     Falafel Restaurant  
4287           Zoo Exhibit            Pizza Place

In [110]:

london_grouped_clustering.loc[london_grouped_clustering['Cluster Labels'] == 4, london_grouped_clustering.columns[[1] + list(range(5, london_grouped_clustering.shape[1]))]].head()

Avg_Price 1st Most Common Venue        2nd Most Common Venue  \
390   2435000.0                   NaN                          NaN   
422   2400000.0     Convenience Store                   Donut Shop   
1635  2397132.0     Convenience Store                  Coffee Shop   
1800  2400000.0           Art Gallery  Eastern European Restaurant   
2161  2425000.0                 Hotel           Italian Restaurant   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
390                    NaN                   NaN                   NaN   
422       Storage Facility  Fast Food Restaurant                  Farm   
1635        Breakfast Spot  Gym / Fitness Center   Sporting Goods Shop   
1800     Electronics Store    English Restaurant           Escape Room   
2161            Restaurant     French Restaurant                Garden   

     6th Most Common Venue     7th Most Common Venue 8th Most Common Venue  \
390                    NaN                       NaN                   NaN   
422      Electronics Store        English Restaurant           Escape Room   
1635              Creperie      Fast Food Restaurant           Escape Room   
1800           Event Space                   Exhibit               Factory   
2161     Indian Restaurant  Mediterranean Restaurant    Chinese Restaurant   

     9th Most Common Venue 10th Most Common Venue  
390                    NaN                    NaN  
422            Event Space                Exhibit  
1635           Event Space                Exhibit  
1800    Falafel Restaurant                   Farm  
2161                   Pub         Clothing Store

### Results and Discussion section


First of all, even though the London Housing Market may be in a rut, it is still an "ever-green" for business affairs.

We may discuss our results under two main perspectives.

First, we may examine them according to neighborhoods/London areas. It is interesting to note that, although West London (Notting Hill, Kensington, Chelsea, Marylebone) and North-West London (Hampsted) might be considered highly profitable venues to purchase a real estate according to amenities and essential facilities surrounding such venues i.e. elementary schools, high schools, hospitals & grocery stores, South-West London (Wandsworth, Balham) and North-West London (Isliington) are arising as next future elite venues with a wide range of amenities and facilities. Accordingly, one might target under-priced real estates in these areas of London in order to make a business affair.

Second, we may analyze our results according to the five clusters we have produced. Even though, all clusters could praise an optimal range of facilities and amenities, we have found two main patterns. The first pattern we are referring to, i.e. Clusters 0, 2 and 4, may target home buyers prone to live in 'green' areas with parks, waterfronts. Instead, the second pattern we are referring to, i.e. Clusters 1 and 3, may target individuals who love pubs, theatres and soccer.

### Conclusion


To sum up, according to Bloomberg News, the London Housing Market is in a rut. It is now facing a number of different headwinds, including the prospect of higher taxes and a warning from the Bank of England that U.K. home values could fall as much as 30 percent in the event of a disorderly exit from the European Union. In this scenario, it is urgent to adopt machine learning tools in order to assist homebuyers clientele in London to make wise and effective decisions. As a result, the business problem we were posing was: how could we provide support to homebuyers clientele in to purchase a suitable real estate in London in this uncertain economic and financial scenario?

To solve this business problem, we clustered London neighborhoods in order to recommend venues and the current average price of real estate where homebuyers can make a real estate investment. We recommended profitable venues according to amenities and essential facilities surrounding such venues i.e. elementary schools, high schools, hospitals & grocery stores.

First, we gathered data on London properties and the relative price paid data were extracted from the HM Land Registry (http://landregistry.data.gov.uk/). Moreover, to explore and target recommended locations across different venues according to the presence of amenities and essential facilities, we accessed data through FourSquare API interface and arranged them as a data frame for visualization. By merging data on London properties and the relative price paid data from the HM Land Registry and data on amenities and essential facilities surrounding such properties from FourSquare API interface, we were able to recommend profitable real estate investments.

Second, The Methodology section comprised four stages: 1. Collect Inspection Data; 2. Explore and Understand Data; 3. Data preparation and preprocessing; 4. Modeling. In particular, in the modeling section, we used the k-means clustering technique as it is fast and efficient in terms of computational cost, is highly flexible to account for mutations in real estate market in London and is accurate.

Finally, we drew the conclusion that even though the London Housing Market may be in a rut, it is still an "ever-green" for business affairs. We discussed our results under two main perspectives. First, we examined them according to neighborhoods/London areas. although West London (Notting Hill, Kensington, Chelsea, Marylebone) and North-West London (Hampsted) might be considered highly profitable venues to purchase a real estate according to amenities and essential facilities surrounding such venues i.e. elementary schools, high schools, hospitals & grocery stores, South-West London (Wandsworth, Balham) and North-West London (Isliington) are arising as next future elite venues with a wide range of amenities and facilities. Accordingly, one might target under-priced real estates in these areas of London in order to make a business affair. Second, we analyzed our results according to the five clusters we produced. While Clusters 0, 2 and 4 may target home buyers prone to live in 'green' areas with parks, waterfronts, Clusters 1 and 3 may target individuals who love pubs, theatres and soccer.